# Домашнее задание
## Параллельные вычисления

Тема: "Решение задачи линейного программирования при помощи параллельного варианта симплекс-метода"

Выполнили:
- Зимин Григорий Сергеевич, ИУ8-112
- Александров Алексей Н., ИУ8-114
- Сакулин Даниил Игоревич, ИУ8-115

In [1]:
import logging
from pathlib import Path

from src.simplex.simplex_problem import SimplexProblem, Solution

In [2]:
logging.basicConfig(level=logging.INFO, format='%(message)s')

In [3]:
problem = SimplexProblem(Path("input_LLP.json"))

F = c⋅x -> max,
Ax <= b,
x1,x2, ..., xn >= 0
c^T = [-1 -1],
A =
[[0 8]
 [9 7]],
b^T = [1 1].
Используем <class 'src.simplex.simplex_table.SimplexTable'> (GPU: False)


In [4]:
%%time
solution: Solution = problem.solve()

Процесс решения:
Поиск опорного решения: 
Исходная симплекс-таблица:
+----+--------+--------+--------+
|    |  Si0   |   x1   |   x2   |
+----+--------+--------+--------+
| x3 | 1.0000 | 0.0000 | 8.0000 |
| x4 | 1.0000 | 9.0000 | 7.0000 |
| F  | 0.0000 | 1.0000 | 1.0000 |
+----+--------+--------+--------+
Опорное решение найдено!
x1 = x2 = 0, 
x3 = 1.000, x4 = 1.000
Целевая функция: F = 0.000
Поиск оптимального решения:
Разрешающая строка: x4
Разрешающий столбец: x1
+----+---------+---------+--------+
|    |   Si0   |    x4   |   x2   |
+----+---------+---------+--------+
| x3 |  1.0000 | -0.0000 | 8.0000 |
| x1 |  0.1111 |  0.1111 | 0.7778 |
| F  | -0.1111 | -0.1111 | 0.2222 |
+----+---------+---------+--------+
Разрешающая строка: x3
Разрешающий столбец: x2
+----+---------+---------+---------+
|    |   Si0   |    x4   |    x3   |
+----+---------+---------+---------+
| x2 |  0.1250 | -0.0000 |  0.1250 |
| x1 |  0.0139 |  0.1111 | -0.0972 |
| F  | -0.1389 | -0.1111 | -0.0278 |
+----+--

CPU times: user 25.8 ms, sys: 5.86 ms, total: 31.7 ms
Wall time: 26.7 ms


In [5]:
problem = SimplexProblem(Path("input_LLP.json"), use_gpu=True)

F = c⋅x -> max,
Ax <= b,
x1,x2, ..., xn >= 0
c^T = [-1 -1],
A =
[[0 8]
 [9 7]],
b^T = [1 1].
Используем <class 'src.simplex.gpu_simplex_table.GPUSimplexTable'> (GPU: True)


In [6]:
%%time
solution: Solution = problem.solve()

Процесс решения:
Поиск опорного решения: 
Исходная симплекс-таблица:
+----+-----+-----+-----+
|    | Si0 |  x1 |  x2 |
+----+-----+-----+-----+
| x3 | 1.0 | 0.0 | 8.0 |
| x4 | 1.0 | 9.0 | 7.0 |
| F  | 0.0 | 1.0 | 1.0 |
+----+-----+-----+-----+
Опорное решение найдено!
x1 = x2 = 0, 
x3 = 1.000, x4 = 1.000
Целевая функция: F = 0.000
Поиск оптимального решения:
Разрешающая строка: x4
Разрешающий столбец: x1
+----+---------------------+---------------------+--------------------+
|    |         Si0         |          x4         |         x2         |
+----+---------------------+---------------------+--------------------+
| x3 |         1.0         |         -0.0        |        8.0         |
| x1 |  0.1111111111111111 |  0.1111111111111111 | 0.7777777777777778 |
| F  | -0.1111111111111111 | -0.1111111111111111 | 0.2222222222222222 |
+----+---------------------+---------------------+--------------------+
Разрешающая строка: x3
Разрешающий столбец: x2
+----+----------------------+------------

CPU times: user 138 ms, sys: 25.6 ms, total: 163 ms
Wall time: 156 ms


In [10]:
import json
import numpy as np
import time
from pathlib import Path

from prettytable import PrettyTable

from src.simplex.simplex_problem import SimplexProblem

def generate_lp_input(num_vars, num_constraints):
    # Генерация коэффициентов целевой функции
    obj_func_coffs = np.random.rand(num_vars).tolist()
    
    # Генерация системы ограничений
    constraint_system_lhs = np.random.rand(num_constraints, num_vars).tolist()
    constraint_system_rhs = np.random.rand(num_constraints).tolist()
    
    # Формирование JSON-структуры
    lp_input = {
        "obj_func_coffs": obj_func_coffs,
        "constraint_system_lhs": constraint_system_lhs,
        "constraint_system_rhs": constraint_system_rhs,
        "func_direction": "max"
    }
    
    return lp_input

def benchmark_lp_solver(num_vars_list, num_constraints_list):
    # Создание таблицы для результатов
    table = PrettyTable()
    table.field_names = ["Num Variables", "Num Constraints", "CPU Time (ms)", "GPU Time (ms)"]

    for num_vars, num_constraints in zip(num_vars_list, num_constraints_list):
        # Генерация входных данных
        lp_input = generate_lp_input(num_vars, num_constraints)
        
        # Сохранение входных данных в JSON файл
        input_file_path = Path("input_LLP.json")
        with open(input_file_path, 'w') as f:
            json.dump(lp_input, f)
        
        # Решение задачи без GPU
        problem_cpu = SimplexProblem(input_file_path)
        start_time = time.time()
        solution_cpu = problem_cpu.solve()
        cpu_time = (time.time() - start_time) * 1000  # Время в миллисекундах
        
        # Решение задачи с GPU
        problem_gpu = SimplexProblem(input_file_path, use_gpu=True)
        start_time = time.time()
        solution_gpu = problem_gpu.solve()
        gpu_time = (time.time() - start_time) * 1000  # Время в миллисекундах
        
        # Добавление результатов в таблицу
        table.add_row([num_vars, num_constraints, f"{cpu_time:.4f}", f"{gpu_time:.4f}"])

    print(table)

# Пример использования
num_vars_list = [2, 5, 10, 100]  # Список размерностей переменных
num_constraints_list = [2, 5, 10, 100]  # Список размерностей ограничений

benchmark_lp_solver(num_vars_list, num_constraints_list)

F = c⋅x -> max,
Ax <= b,
x1,x2, ..., xn >= 0
c^T = [-0.77180817 -0.54084102],
A =
[[0.27786024 0.45086029]
 [0.16188653 0.86201182]],
b^T = [0.01074633 0.6598657 ].
Используем <class 'src.simplex.simplex_table.SimplexTable'> (GPU: False)
Процесс решения:
Поиск опорного решения: 
Исходная симплекс-таблица:
+----+--------+--------+--------+
|    |  Si0   |   x1   |   x2   |
+----+--------+--------+--------+
| x3 | 0.0107 | 0.2779 | 0.4509 |
| x4 | 0.6599 | 0.1619 | 0.8620 |
| F  | 0.0000 | 0.7718 | 0.5408 |
+----+--------+--------+--------+
Опорное решение найдено!
x1 = x2 = 0, 
x3 = 0.011, x4 = 0.660
Целевая функция: F = 0.000
Поиск оптимального решения:
Разрешающая строка: x3
Разрешающий столбец: x1
+----+---------+---------+---------+
|    |   Si0   |    x3   |    x2   |
+----+---------+---------+---------+
| x1 |  0.0387 |  3.5989 |  1.6226 |
| x4 |  0.6536 | -0.5826 |  0.5993 |
| F  | -0.0298 | -2.7777 | -0.7115 |
+----+---------+---------+---------+
Оптимальное решение найдено!
x3 

+---------------+-----------------+---------------+---------------+
| Num Variables | Num Constraints | CPU Time (ms) | GPU Time (ms) |
+---------------+-----------------+---------------+---------------+
|       2       |        2        |    13.7460    |    26.7823    |
|       5       |        5        |    19.0716    |    24.3328    |
|       10      |        10       |    59.2194    |    247.8418   |
|      100      |       100       |   3051.5401   |   12764.0133  |
+---------------+-----------------+---------------+---------------+
